In [1]:
%pip install --upgrade openai
%pip install --upgrade tqdm

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.1.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.1.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
from openai import OpenAI
from tqdm import tqdm

from src.helper_func.project_util import *

import time
import os

## Preparation

In [3]:
def setup(filepath):
    """
    Sets up the project configuration, reads the input file, transforms the graph, and prepares the OpenAI client arguments.

    Args:
        filepath (str): The path to the configuration file.

    Returns:
        tuple: A tuple containing seven elements:
            - project_name (str): The name of the project.
            - project_desc (str): The description of the project.
            - graph (dict): The graph data read from the input file.
            - nodes (dict): The nodes in the transformed graph.
            - edges (dict): The edges in the transformed graph.
            - client_args (dict): The arguments for the OpenAI client.
            - model (str): The OpenAI model to be used.
    """
        
    config = read_ini_file(filepath)
    project_name = config['project']['name']
    project_desc = config['project']['desc']
    ifile = config['project']['ifile']
    
    graph = read_json_file(ifile)
    nodes,edges = transform_graph(graph)
    
    client_args = dict()

    if 'apikey' in config['openai']:
        client_args['api_key'] = config['openai']['apikey']
    if 'apibase' in config['openai']:
        client_args['base_url'] = config['openai']['apibase']
    if 'model' in config['openai']:
        model = config['openai']['model']
    else:
        model = "gpt-3.5-turbo"
    
    return project_name, project_desc, graph, nodes, edges, client_args, model

In [4]:
def elements_preparation(nodes, edges):
    """
    Prepares the elements of a software project for Automated Source Code Summarization (ASCS) and layering.

    Args:
        nodes (dict): A dictionary representing the nodes in the software knowledge graph, where each node is a package, class, or method.
        edges (dict): A dictionary representing the edges in the software knowledge graph, where each edge represents a relationship between two nodes.

    Returns:
        tuple: A tuple containing two elements:
            - hierarchy (dict): A hierarchy of packages, classes, and methods in the project, where each package contains classes and each class contains methods.
            - nodes (dict): The updated nodes dictionary with added 'description' key for each method, class, and package.
    """
    
    methods = sorted(find_paths(edges['contains'], edges['hasScript']))
    print('Methods count: {}'.format(len(methods)))
    classes = sorted({(pkg,clz) for pkg,clz,_ in methods})
    print('Classes count: {}'.format(len(classes)))
    packages = sorted({pkg for pkg,_ in classes})
    print('Packages count: {}'.format(len(packages)))
    
    for _,_,met_id in methods:
        nodes[met_id]['properties']['description'] = None
    for _,cls_id in classes:
        nodes[cls_id]['properties']['description'] = None
    for pkg_id in packages:
        nodes[pkg_id]['properties']['description'] = None
    
    hierarchy = {
        pkg_id: { 
            cls_id: [
                met_id for _,c,met_id in methods if c == cls_id
            ] for p,cls_id in classes if p == pkg_id
        } for pkg_id in packages
    }
    
    print('Mapping count: {}'.format(len(hierarchy)))
       
    return hierarchy, nodes

## Prompt Template

In [5]:
method_prompt_template = '''This is method `{op_name}` of {struct_kind} `{struct_name}`:

```java
{op_src}
```

Explain the above method on the following aspects:

{{ description: "Describe the functionality of the method in one sentence.",
  parameters: [ {{ name:..., type:..., description:... }}, ... ],
  returns: {{ type:..., description: ... }}, // In case of a constructor, consider the constructed class as the return type.
  reason: "Explain, in one sentence, the reason why the method is provided or the design rationale of the method.",
  howToUse: "Describe the usage or the expected set-up of using the method in less than 3 sentences.",
  howItWorks: "Describe the implementation details of the method in less than 5 sentences.",
  assertions: {{ preConditions: ["pre-conditions of the method", ...], postConditions: ["pre-conditions of the method", ...] }},
  layer:...,
  layerReason:...
}}

For the `layer`, fill the value with one of the following architectural layer which functionality is exhibited by the method source code:
- **Presentation Layer**: Manages the user interface, defines UI elements and behavior, displays information, responds to user input, and updates views.
- **Service Layer**: Controls the application flow, orchestrates domain operations, connects UI events with domain logic, and synchronizes domain changes with the UI.
- **Domain Layer**: Handles business logic, represents domain data and behavior, and performs necessary computations for domain operations.
- **Data Source Layer**: Interacts with databases, filesystems, hardware, messaging systems, or other data sources, performs CRUD operations, handles data conversion, and ensures data integrity.

In `layerReason`, explain why this method fits your layer of choice but not the other layers.

Respond with a well-formatted JSON object. Do not use any quote marks ("'`) within the JSON values.'''

In [6]:
class_prompt_template = '''A Java {struct_type} `{struct_name}` specializes the following class(es) or interface(s):

{ancestors}

This {struct_type} contains the following field(s) and method(s):

Fields:

{fields}

Methods:

{methods}

Explain the above {struct_type} on the following aspects:

{{ description: "Describe the responsibility of the {struct_type} in one sentence.", 
  roleStereotype:..., 
  roleStereotypeReason:...,
  layer:...,
  layerReason:... }}

For the `roleStereotype`, fill the value with one of the following role stereotypes which responsibility is exhibited by the {struct_type}:
- **Information Holder**: Responsible for knowing facts and providing information to other objects. POJOs and Java Beans are usually information holders.
- **Service Provider**: Responsible for handling requests and performing specific services. It usually implements a specific interface with a small number of methods. Concrete strategies are service providers.
- **Structurer**: Responsible for managing relationships and constraints among related things. It is usually a collection or mapping of some sort.
- **Controller**: Responsible for making decisions, directing the work of others, and handling important events. It directs the flow of the application or business process.
- **Coordinator**: Responsible for managing the actions of a group of workers and facilitating communication and work of other objects. It delegates requests to other objects. Very abstract classes and interfaces might be coordinators as they delegate the work to subclasses.
- **User Interfacer**: Responsible for transmitting user requests for action or display/render information that can be updated. It handles interactions with users.
- **External Interfacer**: Responsible for loading and storing information from/to external services, including database systems, web services, filesystems, hardware, etc.
- **Internal Interfacer**: Responsible for interfacing between two subsystems. It may bundle together information of requests from a group of objects to be sent to another object. Abstract adapters, bridges, facades, and proxies are internal interfacers.

In `roleStereotypeReason`, explain why this {struct_type} fits your role stereotype of choice but not the other role stereotypes.

For the `layer`, consider the functionalities of architectural layers below:
- **Presentation Layer**: Manages the user interface, defines UI elements and behavior, displays information, responds to user input, and updates views. Typically (but not only) contains objects with 'User Interfacer' role stereotypes.
- **Service Layer**: Controls the application flow, orchestrates domain operations, connects UI events with domain logic, and synchronizes domain changes with the UI. Typically (but not only) contains objects with 'Coordinator' and '(Application) Controller' role stereotypes.
- **Domain Layer**: Handles business logic, represents domain data and behavior, and performs necessary computations for domain operations. Typically (but not only) contains objects with 'Information Holder', 'Service Provider', 'Structurer', 'Coordinator', and '(Domain) Controller' role stereotypes.
- **Data Source Layer**: Interacts with databases, filesystems, hardware, messaging systems, or other data sources, performs CRUD operations, handles data conversion, and ensures data integrity. Typically (but not only) contains objects with 'External Interfacer' role stereotypes.

In `layerReason`, explain why this {struct_type} fits your layer of choice but not the other layers.

Respond with a well-formatted JSON object. Do not use any quote marks ("'`) within the JSON values. In the `description`, do not mention the name of the role stereotype or layer.'''

In [7]:
package_prompt_template = '''Given a Java package `{pkg_name}` containing the following classes:

{classes}

Explain the above package on the following aspects:

{{ description: "Describe the purpose of the package in one sentence.", 
  layer:...,
  layerReason:... }}

For the `layer`, consider the functionalities of architectural layers below:
- **Presentation Layer**: Manages the user interface, defines UI elements and behavior, displays information, responds to user input, and updates views. Typically (but not only) contains classes with 'User Interfacer' role stereotypes.
- **Service Layer**: Controls the application flow, orchestrates domain operations, connects UI events with domain logic, and synchronizes domain changes with the UI. Typically (but not only) contains classes with 'Coordinator' and '(Application) Controller' role stereotypes.
- **Domain Layer**: Handles business logic, represents domain data and behavior, and performs necessary computations for domain operations. Typically (but not only) contains classes with 'Information Holder', 'Service Provider', 'Structurer', 'Coordinator', and '(Domain) Controller' role stereotypes.
- **Data Source Layer**: Interacts with databases, filesystems, hardware, messaging systems, or other data sources, performs CRUD operations, handles data conversion, and ensures data integrity. Typically (but not only) contains objects with 'External Interfacer' role stereotypes.

In `layerReason`, explain why this package fits your layer of choice but not the other layers.

Respond with a well-formatted JSON object. Do not use any quote marks ("'`) within the JSON values. In the `description`, do not mention the name of the layer.'''

## Helper Function

In [8]:
def lower1(s):
    """
    Converts the first character of a string to lowercase.

    Args:
        s (str): The input string.

    Returns:
        str: The string with the first character converted to lowercase. If the input string is empty, it is returned as is.
    """
    if not s:
        return s
    return s[0].lower() + s[1:]

def describe(node):
    """
    Generates a description for a node in the software knowledge graph.

    Args:
        node (dict): The node for which to generate a description.

    Returns:
        str: A string containing the description of the node, formatted as a series of key-value pairs.
    """
    keys = 'description,reason,howToUse,howItWorks,assertions,roleStereotype,layer'.split(',')
    desc = ''
    for key in keys:
        if key in node['properties']:
            desc += f"**{key}**: {str(node['properties'][key])}. "
    return desc

## ASCS and DSAR function template

In [9]:
def ascs_and_layering(project_name, model, client, hierarchy, nodes, edges):
    """
    This function performs Automated Source Code Summarization (ASCS) and layering on a given software project.

    Args:
        project_name (str): The name of the software project.
        model (str): The OpenAI model to be used for generating completions.
        client (openai.Client): The OpenAI client instance for API calls.
        hierarchy (dict): A dictionary representing the hierarchy of packages, classes, and methods in the project.
        nodes (dict): A dictionary representing the nodes in the software knowledge graph, where each node is a package, class, or method.
        edges (dict): A dictionary representing the edges in the software knowledge graph, where each edge represents a relationship between two nodes.

    Returns:
        dict: The updated nodes dictionary with added descriptions for each method and class.
    """
    
    # Initialize current package and class to None
    current_pkg = None
    current_cls = None

    # If True: do not call the API, just print the prompts
    only_print_prompt = False
    
    # Initialize timestamp of the log file
    timestr = time.strftime("%Y%m%d-%H%M%S")
    
    # Open a log file to write the output
    with open(f'1-ASCS-and-DeductiveSAR/ascs-dsar-{project_name}-{model}-{timestr}.log', 'a', encoding="utf-8") as file:
        
        try:
            # Iterate over each package in the hierarchy
            for pkg_id,pkg_data in tqdm(hierarchy.items(), desc="Processing packages", position=0):
                # Write the package ID to the file
                file.write(f'# {pkg_id}\n')
                # Get the package node from the nodes dictionary
                package = nodes[pkg_id]
    
                # Iterate over each class in the current package
                for cls_id,cls_data in tqdm(pkg_data.items(), desc="Processing classes", position=1, leave=False):    
                    # Write the class ID to the file
                    file.write(f'\t* {cls_id}\n')
                    # Get the class node from the nodes dictionary
                    clasz = nodes[cls_id]
                    # Get the class name and kind from the class properties
                    class_name = clasz['properties']['qualifiedName']
                    class_kind = clasz['properties']['kind']
                    # Convert the class kind to a more human-readable format
                    if class_kind == 'enumeration':
                        class_kind = 'enum'
                    elif class_kind == 'abstract':
                        class_kind = 'abstract class'
    
                    # Iterate over each method in the current class
                    for met_id in tqdm(cls_data, desc='Processing methods', position=2, leave=False):
                        # Check if the method has a description
                        if not 'description' in nodes[met_id]['properties'] \
                                or not nodes[met_id]['properties']['description']:
                            # Write the method ID to the file
                            file.write(f'\t\t- {met_id}\n')
                            # Get the method node from the nodes dictionary
                            method = nodes[met_id]
                            # Get the method name and source code from the method properties
                            method_name = method['properties']['simpleName']
                            method_src = remove_java_comments(method['properties']['sourceText'])
    
                            # Format the prompt for the method
                            prompt = method_prompt_template.format(
                                op_name= method_name, 
                                struct_kind= class_kind, 
                                struct_name= class_name, 
                                op_src= method_src)
                            # Write the prompt to the file
                            file.write('\t\t\t' + prompt.replace('\n', '\n\t\t\t') + "\n")
                            file.write("\n")
                            
                            # If only_print_prompt is False, generate a completion for the prompt
                            if not only_print_prompt:
                                response = None
                                try:
                                    # Generate a completion using the OpenAI API
                                    response = client.chat.completions.create(
                                        model=model,
                                        response_format= { "type": "json_object" },
                                        messages=[
                                            {"role": "user","content": prompt}, 
                                        ],
                                        max_tokens=1024, # stop=[". "],
                                        temperature=0)
                                    # Get the content of the response
                                    description = response.choices[0].message.content
                                except:
                                    # If an error occurs, set the description to an empty dictionary
                                    description = '{}'
                                    print(response)
                                    
                                try:
                                    # Try to parse the description as JSON
                                    description = json.loads(description)
                                except:
                                    # If an error occurs, set the description to an empty dictionary
                                    description = dict()
                                
                                # Write the description to the file
                                file.write('\t\t\t'+ prettify_json(description).replace('\n', '\n\t\t\t') + "\n")
                                file.write("\n")
                                
                                # Iterate over each key in the description
                                for key in description:
                                    # Ignore keys that end with 'Reason'
                                    if key.endswith('Reason'):
                                        pass
                                    # If the key is 'parameters', update the description of each parameter
                                    elif lower1(key) == 'parameters':
                                        for parameter in description[key]:
                                            param_id = method['id']+'.'+parameter['name']
                                            if param_id in nodes:
                                                nodes[param_id]['properties']['description'] = parameter.get('description', None)
                                    # For other keys, update the corresponding property of the method
                                    else:
                                        method['properties'][lower1(key)] = description[key]
                        
                        # If a 'stop' file exists, stop the iteration
                        if os.path.exists('stop'):
                            raise StopIteration
    
                    # Get the ancestors and fields of the current class
                    ancestors = {edge['target'] for edge in edges['specializes'] if edge['source'] == cls_id}
                    fields = {edge['target'] for edge in edges['hasVariable'] if edge['source'] == cls_id}
                    # Remove Java comments from the field source text
                    fields = [' '.join(remove_java_comments(nodes[field]['properties']['sourceText']).split()) for field in fields]
    
                    # Format the prompt for the class
                    prompt = class_prompt_template.format(
                            struct_type=class_kind, 
                            struct_name=class_name, 
                            ancestors="\n".join([f"- `{ancestor}`" for ancestor in ancestors]) if ancestors else "(none)",
                            fields="\n".join([f"- `{field}`" for field in fields]) if fields else "(none)",
                            methods="\n".join([f"- `{nodes[met_id]['properties']['simpleName']}`: {describe(nodes[met_id])}" 
                                    for met_id in cls_data])) if cls_data else "(none)"
                    # Write the prompt to the file
                    file.write('\t\t' + prompt.replace('\n', '\n\t\t') + "\n")
                    file.write("\n")
                    
                    # If only_print_prompt is False, generate a completion for the prompt
                    if not only_print_prompt:
                        response = None
                        try:
                            # Generate a completion using the OpenAI API
                            response = client.chat.completions.create(
                                model=model,
                                response_format= { "type": "json_object" },
                                messages=[
                                    {"role": "user", "content": prompt}, 
                                ],
                                max_tokens=1024, 
                                temperature=0)
                            # Get the content of the response
                            description = response.choices[0].message.content
                        except:
                            # If an error occurs, set the description to an empty dictionary
                            description = "{}"
                            # Write the response to the file
                            file.write(str(response) + "\n")
                            
                        try:
                            # Try to parse the description as JSON
                            description = json.loads(description)
                        except:
                            # If an error occurs, set the description to an empty dictionary
                            description = dict()
                            
                        # Write the description to the file
                        file.write('\t\t'+ prettify_json(description).replace('\n', '\n\t\t') + "\n")
                        file.write("\n")
                        
                        # Iterate over each key in the description
                        for key in description:
                            # Ignore keys that end with 'Reason'
                            if key.endswith('Reason'):
                                pass
                            # For other keys, update the corresponding property of the class
                            else:
                                clasz['properties'][lower1(key)] = description[key]
                            
                    # Flush the file buffer
                    file.flush()
                    # If a 'stop' file exists, stop the iteration
                    if os.path.exists('stop'):
                        raise StopIteration
    
                # Format the prompt for the package
                prompt = package_prompt_template.format(
                    pkg_name= package['properties']['qualifiedName'],
                    classes= "\n".join([f"- {nodes[cls_id]['properties']['kind']} `{nodes[cls_id]['properties']['qualifiedName']}`: {describe(nodes[cls_id])}" 
                                    for cls_id, _ in pkg_data.items()])
                )
                # Write the prompt to the file
                file.write('\t' + prompt.replace('\n', '\n\t') + "\n")
                file.write("\n")
                
                # If only_print_prompt is False, generate a completion for the prompt
                if not only_print_prompt:
                    response = None
                    try:
                        # Generate a completion using the OpenAI API
                        response = client.chat.completions.create(
                            model=model,
                            response_format= { "type": "json_object" },
                            messages=[
                                {"role": "user", "content": prompt}, 
                            ],
                            max_tokens=1024, 
                            temperature=0)
                        # Get the content of the response
                        description = response.choices[0].message.content
                    except:
                        # If an error occurs, set the description to an empty dictionary
                        description = '{}'
                        # Write the response to the file
                        file.write(f'{str(response)}\n')
                        
                    try:
                        # Try to parse the description as JSON
                        description = json.loads(description)
                    except:
                        # If an error occurs, set the description to an empty dictionary
                        description = dict()
                        
                    # Write the description to the file
                    file.write('\t' + prettify_json(description).replace('\n', '\n\t') + "\n")
                    file.write("\n")
                    
                    # Iterate over each key in the description
                    for key in description:
                        # Ignore keys that end with 'Reason'
                        if not key.endswith('Reason'):
                            # For other keys, update the corresponding property of the package
                            package['properties'][lower1(key)] = description[key]
                
                # If a 'stop' file exists, stop the iteration
                if os.path.exists('stop'):
                    raise StopIteration
    
        # If a StopIteration exception is raised, pass it
        except StopIteration:
            pass
    
    # Return the updated nodes dictionary
    return nodes, timestr

# Case Study 1: JHotDraw v5.1

In [10]:
project_name, project_desc, graph, nodes, edges, cliet_args, model = setup('config-jhotdraw-v5.1.ini')

In [11]:
hierarchy, nodes = elements_preparation(nodes, edges)

Methods count: 1327
Classes count: 155
Packages count: 11
Mapping count: 11


In [15]:
client = OpenAI(**cliet_args)
print(client.base_url)
print(model)

https://api.openai.com/v1/
gpt-4o-mini


In [16]:
# test the LLM server---create a completion
completion = client.chat.completions.create(
    model=model,
    messages=[{"role":"user","content":"Hello, world!"}],
    temperature=0
)
# print the completion
print(completion.choices[0].message.content)

Hello! How can I assist you today?


In [17]:
nodes, timestr = ascs_and_layering(project_name, model, client, hierarchy, nodes, edges)

Processing classes:   0%|          | 0/2 [00:00<?, ?it/s]

Processing methods:   0%|          | 0/35 [00:00<?, ?it/s]

Processing methods:   3%|▎         | 1/35 [00:03<02:05,  3.71s/it]

Processing methods:   6%|▌         | 2/35 [00:07<02:12,  4.01s/it]

Processing methods:   9%|▊         | 3/35 [00:11<02:05,  3.91s/it]

Processing methods:  11%|█▏        | 4/35 [00:15<02:01,  3.93s/it]

Processing methods:  14%|█▍        | 5/35 [00:19<01:59,  3.99s/it]

Processing methods:  17%|█▋        | 6/35 [00:24<02:02,  4.23s/it]

Processing methods:  20%|██        | 7/35 [00:29<02:05,  4.49s/it]

Processing methods:  23%|██▎       | 8/35 [00:35<02:17,  5.10s/it]

Processing methods:  26%|██▌       | 9/35 [00:39<01:59,  4.60s/it]

Processing methods:  29%|██▊       | 10/35 [00:42<01:46,  4.25s/it]

Processing methods:  31%|███▏      | 11/35 [00:47<01:46,  4.45s/it]

Processing methods:  34%|███▍      | 12/35 [00:50<01:33,  4.06s/it]

Processing methods:  37%|███▋      | 13/35 [00:55<01:35,  4.32

In [18]:
nodes

{'CH.ifa.draw.standard.OffsetLocator.locate(CH.ifa.draw.framework.Figure).owner': {'id': 'CH.ifa.draw.standard.OffsetLocator.locate(CH.ifa.draw.framework.Figure).owner',
  'properties': {'simpleName': 'owner',
   'qualifiedName': 'CH.ifa.draw.standard.OffsetLocator.locate(CH.ifa.draw.framework.Figure).owner',
   'kind': 'parameter',
   'metaSrc': 'source code',
   'description': 'The figure whose location is being determined.'},
  'labels': ['Variable']},
 'CH.ifa.draw.samples.javadraw.AnimationDecorator.basicMoveBy(int,int).y': {'id': 'CH.ifa.draw.samples.javadraw.AnimationDecorator.basicMoveBy(int,int).y',
  'properties': {'simpleName': 'y',
   'qualifiedName': 'CH.ifa.draw.samples.javadraw.AnimationDecorator.basicMoveBy(int,int).y',
   'kind': 'parameter',
   'metaSrc': 'source code',
   'description': 'The vertical offset by which the object should be moved.'},
  'labels': ['Variable']},
 'CH.ifa.draw.figures.TextFigure.fOriginY': {'id': 'CH.ifa.draw.figures.TextFigure.fOriginY',
 

In [19]:
graph['elements']['nodes'] = [{'data':node_data} for node_data in nodes.values()]

In [20]:
write_to_json_file(graph, f'../test/output/1-ASCS-and-DeductiveSAR/ascs-dsar-{project_name}-{model}-{timestr}.json')

# Case Study 2: Bitcoin Wallet v6.31

In [11]:
project_name, project_desc, graph, nodes, edges, client_args, model = setup('config-bitcoin-wallet-v6.31.ini')

(project_name, project_desc)

('bitcoin-wallet-v6.31',
 'Bitcoin Wallet, a standalone Bitcoin payment app for your Android device!')

In [12]:
hierarchy, nodes = elements_preparation(nodes, edges)

Methods count: 1280
Classes count: 235
Packages count: 13
Mapping count: 13


In [13]:
client = OpenAI(**client_args)
print(client.base_url)
print(model)

https://api.openai.com/v1/
gpt-4o-mini


In [14]:
# test the LLM server---create a completion
completion = client.chat.completions.create(
    model=model,
    messages=[{"role":"user","content":"Hello, world!"}],
    temperature=0
)
# print the completion
print(completion.choices[0].message.content)

Hello! How can I assist you today?


In [15]:
nodes, timestr = ascs_and_layering(project_name, model, client, hierarchy, nodes, edges)

Processing classes:   0%|          | 0/7 [00:00<?, ?it/s]

Processing methods:   0%|          | 0/36 [00:00<?, ?it/s]

Processing methods:   3%|▎         | 1/36 [00:02<01:40,  2.87s/it]

Processing methods:   6%|▌         | 2/36 [00:08<02:28,  4.37s/it]

Processing methods:   8%|▊         | 3/36 [00:13<02:35,  4.72s/it]

Processing methods:  11%|█         | 4/36 [00:17<02:21,  4.41s/it]

Processing methods:  14%|█▍        | 5/36 [00:21<02:13,  4.29s/it]

Processing methods:  17%|█▋        | 6/36 [00:24<01:57,  3.92s/it]

Processing methods:  19%|█▉        | 7/36 [00:29<01:58,  4.10s/it]

Processing methods:  22%|██▏       | 8/36 [00:33<01:53,  4.06s/it]

Processing methods:  25%|██▌       | 9/36 [00:37<01:50,  4.08s/it]

Processing methods:  28%|██▊       | 10/36 [00:41<01:46,  4.08s/it]

Processing methods:  31%|███       | 11/36 [00:44<01:33,  3.74s/it]

Processing methods:  33%|███▎      | 12/36 [00:46<01:21,  3.42s/it]

Processing methods:  36%|███▌      | 13/36 [00:50<01:22,  3.59

In [16]:
nodes

{'de.schildbach.wallet.ui.WalletBalanceFragment.onCreateOptionsMenu(android.view.Menu,android.view.MenuInflater).inflater': {'id': 'de.schildbach.wallet.ui.WalletBalanceFragment.onCreateOptionsMenu(android.view.Menu,android.view.MenuInflater).inflater',
  'properties': {'simpleName': 'inflater',
   'qualifiedName': 'de.schildbach.wallet.ui.WalletBalanceFragment.onCreateOptionsMenu(android.view.Menu,android.view.MenuInflater).inflater',
   'kind': 'parameter',
   'metaSrc': 'source code',
   'description': 'The MenuInflater used to inflate the menu resource.'},
  'labels': ['Variable']},
 'de.schildbach.wallet.ui.TransactionsAdapter.de.schildbach.wallet.ui.TransactionsAdapter(android.content.Context,int,de.schildbach.wallet.ui.TransactionsAdapter$OnClickListener).context': {'id': 'de.schildbach.wallet.ui.TransactionsAdapter.de.schildbach.wallet.ui.TransactionsAdapter(android.content.Context,int,de.schildbach.wallet.ui.TransactionsAdapter$OnClickListener).context',
  'properties': {'simp

In [17]:
graph['elements']['nodes'] = [{'data':node_data} for node_data in nodes.values()]

In [18]:
write_to_json_file(graph, f'../test/output/1-ASCS-and-DeductiveSAR/ascs-dsar-{project_name}-{model}-{timestr}.json')

# Case Study 3: K9-Mail v5.304

In [10]:
project_name, project_desc, graph, nodes, edges, cliet_args, model = setup('config-k9mail-v5.304.ini')

(project_name, project_desc)

('k9mail-v5.304', 'K-9 Mail is an open-source email client for Android.')

In [11]:
hierarchy, nodes = elements_preparation(nodes, edges)

Methods count: 8032
Classes count: 968
Packages count: 58
Mapping count: 58


In [12]:
client = OpenAI(**cliet_args)
print(client.base_url)
print(model)

https://api.openai.com/v1/
gpt-4o-mini


In [13]:
# test the LLM server---create a completion
completion = client.chat.completions.create(
    model=model,
    messages=[{"role":"user","content":"Hello, world!"}],
    temperature=0
)
# print the completion
print(completion.choices[0].message.content)

Hello! How can I assist you today?


In [14]:
nodes, timestr = ascs_and_layering(project_name, model, client, hierarchy, nodes, edges)

Processing classes:   0%|          | 0/38 [00:00<?, ?it/s]

Processing methods:   0%|          | 0/173 [00:00<?, ?it/s]

Processing methods:   1%|          | 1/173 [00:04<14:00,  4.88s/it]

Processing methods:   1%|          | 2/173 [00:08<12:01,  4.22s/it]

Processing methods:   2%|▏         | 3/173 [00:12<11:29,  4.06s/it]

Processing methods:   2%|▏         | 4/173 [00:18<13:07,  4.66s/it]

Processing methods:   3%|▎         | 5/173 [00:23<13:21,  4.77s/it]

Processing methods:   3%|▎         | 6/173 [00:32<17:56,  6.45s/it]

Processing methods:   4%|▍         | 7/173 [00:38<17:16,  6.25s/it]

Processing methods:   5%|▍         | 8/173 [00:48<20:31,  7.46s/it]

Processing methods:   5%|▌         | 9/173 [00:53<17:49,  6.52s/it]

Processing methods:   6%|▌         | 10/173 [00:57<15:49,  5.83s/it]

Processing methods:   6%|▋         | 11/173 [01:02<15:06,  5.59s/it]

Processing methods:   7%|▋         | 12/173 [01:08<15:04,  5.62s/it]

Processing methods:   8%|▊         | 13/173 [01:

In [15]:
nodes

{'com.fsck.k9.mail.Part.addHeader(java.lang.String,java.lang.String)': {'id': 'com.fsck.k9.mail.Part.addHeader(java.lang.String,java.lang.String)',
  'properties': {'visibility': 'public',
   'simpleName': 'addHeader(java.lang.String,java.lang.String)',
   'qualifiedName': 'com.fsck.k9.mail.Part.addHeader(java.lang.String,java.lang.String)',
   'kind': 'method',
   'sourceText': 'void addHeader(java.lang.String name, java.lang.String value);',
   'docComment': '',
   'metaSrc': 'source code',
   'description': 'The method adds a specified header with a given name and value to a mail part.',
   'returns': {'type': 'void',
    'description': 'This method does not return a value.'},
   'reason': 'The method is provided to allow customization of the headers in a mail part, which is essential for email formatting and protocol compliance.',
   'howToUse': 'To use this method, create an instance of a class that implements the Part interface. Then, call addHeader with the desired header name a

In [16]:
graph['elements']['nodes'] = [{'data':node_data} for node_data in nodes.values()]

In [17]:
write_to_json_file(graph, f'../test/output/1-ASCS-and-DeductiveSAR/ascs-dsar-{project_name}-{model}-{timestr}.json')

# Case Study 4: SweetHome3D v5.6

In [ ]:
project_name, project_desc, graph, nodes, edges, client_args, model = setup('config-sweethome3d-v5.6.ini')

(project_name, project_desc)

In [ ]:
hierarchy, nodes = elements_preparation(nodes, edges)

In [ ]:
client = OpenAI(**client_args)
print(client.base_url)
print(model)

In [ ]:
# test the LLM server---create a completion
completion = client.chat.completions.create(
    model=model,
    messages=[{"role":"user","content":"Hello, world!"}],
    temperature=0
)
# print the completion
print(completion.choices[0].message.content)

In [ ]:
nodes, timestr = ascs_and_layering(project_name, model, client, hierarchy, nodes, edges)

In [ ]:
nodes

In [ ]:
graph['elements']['nodes'] = [{'data':node_data} for node_data in nodes.values()]

In [ ]:
write_to_json_file(graph, f'../test/output/1-ASCS-and-DeductiveSAR/ascs-dsar-{project_name}-{model}-{timestr}.json')